In [1]:
import pandas as pd
from __future__ import absolute_import, division

import os
import time
import numpy as np
import pandas as pd
import gensim
from tqdm import tqdm
import random
import psutil
from multiprocessing import Pool
import multiprocessing as mp
from gensim.models import KeyedVectors
import re
import gc
import pickle
import operator

In [2]:
def get_coefs(word, *arr):
    return word, np.asarray(arr, dtype='float32')


def load_embeddings(path):
    embeddings_index = {}
    f = open(path,encoding='utf8')
    print(f)
    for line in f:
        values = line.split()
        word = ' '.join(values[:-300])
        coefs = np.asarray(values[-300:], dtype='float32')
        embeddings_index[word] = coefs.reshape(-1)
    f.close()
    return embeddings_index

def build_matrix(word_index, path):
    embedding_index = load_embeddings(path)
    embedding_matrix = np.zeros((len(word_index) + 1, 300))
    unknown_words = []
    
    for word, i in word_index.items():
        try:
            embedding_matrix[i] = embedding_index[word]
        except KeyError:
            unknown_words.append(word)
    return embedding_matrix, unknown_words

def build_vocab(sentences, verbose =  True):
    """
    :param sentences: list of list of words
    :return: dictionary of words and their count
    """
#     sentences=str(sentences)
    vocab = {}
    for sentence in tqdm(sentences, disable = (not verbose)):
        for word in sentence:
            try:
                vocab[word] += 1
            except KeyError:
                vocab[word] = 1
    return vocab

def check_coverage(vocab,embeddings_index):
    a = {}
    oov = {}
    k = 0
    i = 0
    for word in tqdm(vocab):
        try:
            a[word] = embeddings_index[word]
            k += vocab[word]
        except:

            oov[word] = vocab[word]
            i += vocab[word]
            pass

    print('Found embeddings for {:.2%} of vocab'.format(len(a) / len(vocab)))
    print('Found embeddings for  {:.2%} of all text'.format(k / (k + i)))
    sorted_x = sorted(oov.items(), key=operator.itemgetter(1))[::-1]

    return a,sorted_x

import string
def text_to_wordlist(text, remove_stopwords=False,stem_words=False,lemma_word=False):
    
    text = str(text)
    text = text.lower().split()
    
    #remove stops
    if remove_stopwords:
        stops = set(stopwords.words("english"))
        text = [w for w in text if not w in stops]
        
    text = " ".join(text)
    
#     text = re.sub(r",",r"",text)
#     text = re.sub(".*?n't"," not",text)
    text=re.sub(r"\'",r"'",text)
    text = re.sub(r" e.g ", " eg ", text)
    text = re.sub(r" b.g ", " bg ", text)
    text = re.sub(r"U.S", "US", text)
    
    text = re.sub(r"sharethefacts{.*?Share The Facts"," ",text)
    
    # stemmer
    if stem_words:
        text = text.split()
        stemmer = SnowballStemmer('english')
        stemmed_words = [stemmer.stem(word) for word in text]
        text = " ".join(stemmed_words)
        
#     text = text.lower()
        
    return text


In [3]:
GLOVE_EMBEDDING_PATH= "../glove/glove6B/glove.6B.300d.txt"
num_models = 2
lstm_units = 128
dense_hidden_units = 4 * lstm_units
max_len = 220
embed_size = 300
max_features = 120000

tic = time.time()
glove_embeddings = load_embeddings(GLOVE_EMBEDDING_PATH)
print(f'loaded {len(glove_embeddings)} word vectors in {time.time()-tic}s')

# %%time
# load = True
# if not load:
names = ["id", "label", "statement", "subject", "speaker", "job", "state", "party",
                                            "barely-true", "false", "half-true", "mostly-true", "pants-fire", "venue","justifikasi"]
    
train= pd.read_csv("../LIAR-PLUS/dataset/train.tsv",delimiter='\t',header=None, error_bad_lines=False,names=names)
test= pd.read_csv("../LIAR-PLUS/dataset/test.tsv",delimiter='\t',header=None, error_bad_lines=False,names=names)
valid= pd.read_csv("../LIAR-PLUS/dataset/valid.tsv",delimiter='\t',header=None, error_bad_lines=False,names=names)
train.dropna(subset=['justifikasi'], how='all', inplace = True)
test.dropna(subset=['justifikasi'], how='all', inplace = True)
# train.dropna()

<_io.TextIOWrapper name='../glove/glove6B/glove.6B.300d.txt' mode='r' encoding='utf8'>
loaded 400001 word vectors in 24.962246656417847s


In [4]:
import string
from nltk.tokenize.treebank import TreebankWordTokenizer

data_train = train['justifikasi']

latin_similar = "’'‘ÆÐƎƏƐƔĲŊŒẞÞǷȜæðǝəɛɣĳŋœĸſßþƿȝĄƁÇĐƊĘĦĮƘŁØƠŞȘŢȚŦŲƯY̨Ƴąɓçđɗęħįƙłøơşșţțŧųưy̨ƴÁÀÂÄǍĂĀÃÅǺĄÆǼǢƁĆĊĈČÇĎḌĐƊÐÉÈĖÊËĚĔĒĘẸƎƏƐĠĜǦĞĢƔáàâäǎăāãåǻąæǽǣɓćċĉčçďḍđɗðéèėêëěĕēęẹǝəɛġĝǧğģɣĤḤĦIÍÌİÎÏǏĬĪĨĮỊĲĴĶƘĹĻŁĽĿʼNŃN̈ŇÑŅŊÓÒÔÖǑŎŌÕŐỌØǾƠŒĥḥħıíìiîïǐĭīĩįịĳĵķƙĸĺļłľŀŉńn̈ňñņŋóòôöǒŏōõőọøǿơœŔŘŖŚŜŠŞȘṢẞŤŢṬŦÞÚÙÛÜǓŬŪŨŰŮŲỤƯẂẀŴẄǷÝỲŶŸȲỸƳŹŻŽẒŕřŗſśŝšşșṣßťţṭŧþúùûüǔŭūũűůųụưẃẁŵẅƿýỳŷÿȳỹƴźżžẓ"
white_list = string.ascii_letters + string.digits + latin_similar + ' '
# white_list += "'"

glove_chars = ''.join([c for c in tqdm(glove_embeddings) if len(c) == 1])
glove_symbols = ''.join([c for c in glove_chars if not c in white_list])
print(glove_symbols)
jigsaw_chars = build_vocab(list(data_train))
jigsaw_symbols = ''.join([c for c in jigsaw_chars if not c in white_list])
print(jigsaw_symbols)
symbols_to_delete = ''.join([c for c in jigsaw_symbols if not c in glove_symbols])
print(symbols_to_delete)
symbols_to_isolate = ''.join([c for c in jigsaw_symbols if c in glove_symbols])
print(symbols_to_isolate)


isolate_dict = {ord(c):f' {c} ' for c in symbols_to_isolate}
remove_dict = {ord(c):f'' for c in symbols_to_delete}


def handle_punctuation(x):
    x=str(x)
    x = x.translate(remove_dict)
    x = x.translate(isolate_dict)
    return x


def handle_contractions(x):
    tokenizer = TreebankWordTokenizer()
    x = tokenizer.tokenize(x)
    x = ' '.join(x)
    return x

def preprocess(x):
    x = text_to_wordlist(x)
    x = handle_punctuation(x)
    x = handle_contractions(x)
    x = x.lower()
    return x



 26%|██▌       | 2651/10205 [00:00<00:00, 26509.77it/s]

,."-():$;_?–%/!`&=—“”#[+¥£|]~\{…½>€}*@<»«、α¼^βφωλσδγθπ„με¾¡ρ¢ψτηƒκ₤⅓иνζ¿χξ⅔в―ο。‚сιರа⅛རསυя›ಕངоو‹уನ˚ದනгරאеತಸകಮ⅜ག₂ව·ಪල¤ὁදкසವಗіរ⅝කལϕནདಲтಯಡಬ¨ъടම‟мಶь⅞ה镇පයнªམ乡තлಟབпសಹ道ɔରതф￥ר王хἡчэзപʃḳшיוಳបʔកбדග⁰дಜש李жєבតס神姬人一ю


100%|██████████| 10205/10205 [00:00<00:00, 26348.99it/s]

.-,"…()“”;$?:— –{#%}_@/* ‪‎‬&!
	•[]+=`½➤\­― ⅔
  ‪‎‬
	•➤­ 
.-,"…()“”;$?:—–{#%}_@/*&![]+=`½\―⅔


In [5]:
data_test = test['justifikasi'].apply(lambda x: preprocess(x))
data_test

0       meantime , engineering experts agree the wall ...
1       she cited layoff notices received by the state...
2       trump said that mccain `` has done nothing to ...
3       but spending still goes up . in addition , man...
4       our rating a democratic party web video making...
5       rhode island ’ s former top cop is setting his...
6       residents in those suburbs do not get a vote b...
7       boehner may be technically correct that biden ...
8       speaking at the democratic national convention...
9       pence said , `` we know that more than half of...
10      there ’ s little concrete evidence that defini...
11      we informed mackowiak of the date conflict . h...
12      the word `` denali `` doesn ’ t show up in swa...
13      a social - media meme says that 57 percent of ...
14      he clearly has some misgivings about residency...
15      in october , it was 4 . 4 percent , according ...
16      as senate president , niehaus is one of the mo...
17      blackb

In [6]:
vocab2 = build_vocab(list(data_test.apply(lambda x:x.lower().split())))
known,unknown = check_coverage(vocab2,glove_embeddings)
print(unknown)
print(known.keys())

100%|██████████| 9185/9185 [00:00<00:00, 1521091.41it/s]

Found embeddings for 98.79% of vocab
Found embeddings for  99.87% of all text
[('vedp', 6), ('rpof', 6), ('pocan', 5), ('grothman', 3), ('jobsohio', 3), ('masto', 3), ("'i", 3), ('punditfact', 3), ('politifactri', 3), ('carlevale', 2), ('noncontraceptive', 2), ('polistina', 2), ('alcantar', 2), ('schatelowitz', 2), ('budish', 2), ('zaring', 2), ('chalkings', 2), ('mediaquant', 2), ('waitlist', 2), ('requestors', 2), ('kleefisch', 2), ('dimassimo', 2), ('bramnick', 2), ('athists', 2), ('hadn', 2), ('burzichelli', 1), ('denseness', 1), ('harambe', 1), ('steineke', 1), ('agrifood', 1), ('ohfood', 1), ('obameter', 1), ("'what", 1), ('wuerker', 1), ("'could", 1), ("'serious", 1), ('keyhani', 1), ('simplifing', 1), ("'complete", 1), ('voterid', 1), ("''the", 1), ("''no", 1), ('lundergan', 1), ('unifications', 1), ('charliecristfl', 1), ('lindbeck', 1), ('joee', 1), ('wev', 1), ('conservativehq', 1), ('rollingwood', 1), ('wedc', 1), ('shorthands', 1), ('schloemer', 1), ('prante', 1), ('unveto

In [7]:
data_for_pos = test['justifikasi'].apply(lambda x: handle_punctuation(x))
data_for_pos

0       Meantime ,  engineering experts agree the wall...
1       She cited layoff notices received by the state...
2       Trump said that McCain  " has done nothing to ...
3       But spending still goes up . In addition ,  ma...
4       Our rating A Democratic Party web video making...
5       Rhode Island’s former top cop is setting his b...
6       Residents in those suburbs do not get a vote b...
7       Boehner may be technically correct that Biden ...
8       Speaking at the Democratic National Convention...
9       Pence said ,   " We know that more than half o...
10      There’s little concrete evidence that definiti...
11      We informed Mackowiak of the date conflict . H...
12      The word  " Denali "  doesn’t show up in Swahi...
13      A social - media meme says that 57 percent of ...
14      He clearly has some misgivings about residency...
15      In October ,  it was 4 . 4 percent ,  accordin...
16      As Senate president ,  Niehaus is one of the m...
17      Blackb

In [8]:
#####################
###   POS TAGS    ###
#####################

import stanfordnlp
import pandas as pd
import pickle
# import data_util as du

# train,test,valid = du.load_dataset()
nlp = stanfordnlp.Pipeline(processors = "tokenize,mwt,lemma,pos")

Use device: gpu
---
Loading: tokenize
With settings: 
{'model_path': '/hdd1/rini.jannati/stanfordnlp_resources/en_ewt_models/en_ewt_tokenizer.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
---
Loading: lemma
With settings: 
{'model_path': '/hdd1/rini.jannati/stanfordnlp_resources/en_ewt_models/en_ewt_lemmatizer.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
Building an attentional Seq2Seq model...
Using a Bi-LSTM encoder
Using soft attention for LSTM.
Finetune all embeddings.
[Running seq2seq lemmatizer with edit classifier]
---
Loading: pos
With settings: 
{'model_path': '/hdd1/rini.jannati/stanfordnlp_resources/en_ewt_models/en_ewt_tagger.pt', 'pretrain_path': '/hdd1/rini.jannati/stanfordnlp_resources/en_ewt_models/en_ewt.pretrain.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
Done loading processors!
---


In [9]:
def get_word(doc):
    doc = nlp(doc)
#     print(doc)
    word=list()
    for sent in doc.sentences:
        for wrd in sent.words:
            print(wrd.text," POSTag: ",wrd.upos)
            word.append(wrd)
#             print(type(wrd))
    return word

nlpst_test_ = data_for_pos.apply(lambda x: get_word(x))




Meantime  POSTag:  NOUN
,  POSTag:  PUNCT
engineering  POSTag:  NOUN
experts  POSTag:  NOUN
agree  POSTag:  VERB
the  POSTag:  DET
wall  POSTag:  NOUN
would  POSTag:  AUX
most  POSTag:  ADV
likely  POSTag:  ADV
take  POSTag:  VERB
years  POSTag:  NOUN
to  POSTag:  PART
complete  POSTag:  VERB
.  POSTag:  PUNCT
Keep  POSTag:  VERB
in  POSTag:  ADP
mind  POSTag:  NOUN
,  POSTag:  PUNCT
too  POSTag:  ADV
,  POSTag:  PUNCT
it  POSTag:  PRON
took  POSTag:  VERB
more  POSTag:  ADJ
than  POSTag:  ADP
six  POSTag:  NUM
years  POSTag:  NOUN
to  POSTag:  PART
build  POSTag:  VERB
roughly  POSTag:  ADV
700  POSTag:  NUM
miles  POSTag:  NOUN
of  POSTag:  ADP
fence  POSTag:  NOUN
and  POSTag:  CCONJ
barriers  POSTag:  NOUN
along  POSTag:  ADP
the  POSTag:  DET
roughly  POSTag:  ADV
2  POSTag:  NUM
,  POSTag:  PUNCT
000  POSTag:  NUM
-  POSTag:  SYM
mile  POSTag:  NOUN
U  POSTag:  NOUN
.  POSTag:  PUNCT
S  POSTag:  X
.  POSTag:  PUNCT
-  POSTag:  PUNCT
Mexico  POSTag:  PROPN
border  POSTag:  NOUN
. 

Residents  POSTag:  NOUN
in  POSTag:  ADP
those  POSTag:  DET
suburbs  POSTag:  NOUN
do  POSTag:  AUX
not  POSTag:  PART
get  POSTag:  VERB
a  POSTag:  DET
vote  POSTag:  NOUN
because  POSTag:  SCONJ
they  POSTag:  PRON
already  POSTag:  ADV
have  POSTag:  AUX
authorized  POSTag:  VERB
sales  POSTag:  NOUN
tax  POSTag:  NOUN
increases  POSTag:  NOUN
for  POSTag:  ADP
their  POSTag:  PRON
towns  POSTag:  NOUN
.  POSTag:  PUNCT
Another  POSTag:  DET
argument  POSTag:  NOUN
by  POSTag:  ADP
proponents  POSTag:  NOUN
is  POSTag:  VERB
that  POSTag:  SCONJ
a  POSTag:  DET
vote  POSTag:  NOUN
against  POSTag:  ADP
the  POSTag:  DET
half  POSTag:  NOUN
-  POSTag:  PUNCT
cent  POSTag:  NOUN
sales  POSTag:  NOUN
tax  POSTag:  NOUN
increase  POSTag:  NOUN
is  POSTag:  AUX
essentially  POSTag:  ADV
a  POSTag:  DET
vote  POSTag:  NOUN
for  POSTag:  ADP
a  POSTag:  DET
property  POSTag:  NOUN
-  POSTag:  PUNCT
tax  POSTag:  NOUN
increase  POSTag:  NOUN
to  POSTag:  PART
fund  POSTag:  VERB
the  POS

We  POSTag:  PRON
informed  POSTag:  VERB
Mackowiak  POSTag:  PROPN
of  POSTag:  ADP
the  POSTag:  DET
date  POSTag:  NOUN
conflict  POSTag:  NOUN
.  POSTag:  PUNCT
He  POSTag:  PRON
later  POSTag:  ADV
told  POSTag:  VERB
us  POSTag:  PRON
that  POSTag:  SCONJ
the  POSTag:  DET
campaign  POSTag:  NOUN
had  POSTag:  AUX
fixed  POSTag:  VERB
the  POSTag:  DET
date  POSTag:  NOUN
and  POSTag:  CCONJ
sent  POSTag:  VERB
new  POSTag:  ADJ
copies  POSTag:  NOUN
of  POSTag:  ADP
the  POSTag:  DET
ad  POSTag:  NOUN
to  POSTag:  ADP
the  POSTag:  DET
outlets  POSTag:  NOUN
running  POSTag:  VERB
the  POSTag:  DET
ads  POSTag:  NOUN
.  POSTag:  PUNCT
The  POSTag:  DET
word  POSTag:  NOUN
"  POSTag:  PUNCT
Denali  POSTag:  PROPN
"  POSTag:  PUNCT
does  POSTag:  AUX
n’t  POSTag:  PART
show  POSTag:  VERB
up  POSTag:  ADP
in  POSTag:  ADP
Swahili  POSTag:  PROPN
,  POSTag:  PUNCT
one  POSTag:  NUM
of  POSTag:  ADP
Kenya  POSTag:  PROPN
’s  POSTag:  PART
two  POSTag:  NUM
national  POSTag:  ADJ
lan

Blackburn  POSTag:  PROPN
said  POSTag:  VERB
a  POSTag:  DET
recent  POSTag:  ADJ
Gallup  POSTag:  PROPN
poll  POSTag:  NOUN
found  POSTag:  VERB
that  POSTag:  SCONJ
72  POSTag:  NUM
percent  POSTag:  NOUN
of  POSTag:  ADP
Americans  POSTag:  PROPN
and  POSTag:  CCONJ
56  POSTag:  NUM
percent  POSTag:  NOUN
of  POSTag:  ADP
Democrats  POSTag:  PROPN
"  POSTag:  PUNCT
say  POSTag:  VERB
the  POSTag:  DET
biggest  POSTag:  ADJ
threat  POSTag:  NOUN
to  POSTag:  ADP
our  POSTag:  PRON
nation  POSTag:  NOUN
's  POSTag:  PART
security  POSTag:  NOUN
is  POSTag:  AUX
big  POSTag:  ADJ
government  POSTag:  NOUN
.  POSTag:  PUNCT
"  POSTag:  PUNCT
She  POSTag:  PRON
got  POSTag:  VERB
the  POSTag:  DET
numbers  POSTag:  NOUN
right  POSTag:  ADV
,  POSTag:  PUNCT
but  POSTag:  CCONJ
the  POSTag:  DET
specific  POSTag:  ADJ
poll  POSTag:  NOUN
only  POSTag:  ADV
offered  POSTag:  VERB
respondents  POSTag:  NOUN
three  POSTag:  NUM
options  POSTag:  NOUN
:  POSTag:  PUNCT
"  POSTag:  PUNCT
big 

Rubio  POSTag:  PROPN
said  POSTag:  VERB
that  POSTag:  SCONJ
Romney  POSTag:  PROPN
was  POSTag:  AUX
"  POSTag:  PUNCT
one  POSTag:  NUM
of  POSTag:  ADP
the  POSTag:  DET
first  POSTag:  ADJ
national  POSTag:  ADJ
Republican  POSTag:  ADJ
leaders  POSTag:  NOUN
to  POSTag:  PART
endorse  POSTag:  VERB
me  POSTag:  PRON
.  POSTag:  PUNCT
"  POSTag:  PUNCT
Romney  POSTag:  PROPN
did  POSTag:  AUX
endorse  POSTag:  VERB
Rubio  POSTag:  PROPN
before  POSTag:  SCONJ
Crist  POSTag:  PROPN
dropped  POSTag:  VERB
out  POSTag:  ADP
of  POSTag:  ADP
the  POSTag:  DET
primary  POSTag:  ADJ
in  POSTag:  ADP
2010  POSTag:  NUM
.  POSTag:  PUNCT
But  POSTag:  CCONJ
it  POSTag:  PRON
was  POSTag:  AUX
clear  POSTag:  ADJ
at  POSTag:  ADP
the  POSTag:  DET
time  POSTag:  NOUN
that  POSTag:  SCONJ
Rubio  POSTag:  PROPN
would  POSTag:  AUX
have  POSTag:  AUX
thumped  POSTag:  VERB
Crist  POSTag:  PROPN
in  POSTag:  ADP
a  POSTag:  DET
primary  POSTag:  ADJ
if  POSTag:  SCONJ
Crist  POSTag:  PROPN
ha

...

Thomas  POSTag:  PROPN
,  POSTag:  PUNCT
the  POSTag:  DET
third  POSTag:  ADJ
-  POSTag:  PUNCT
longest  POSTag:  ADJ
tenured  POSTag:  VERB
justice  POSTag:  NOUN
on  POSTag:  ADP
the  POSTag:  DET
court  POSTag:  NOUN
,  POSTag:  PUNCT
is  POSTag:  AUX
apparently  POSTag:  ADV
old  POSTag:  ADJ
school  POSTag:  NOUN
.  POSTag:  PUNCT
The  POSTag:  DET
experts  POSTag:  NOUN
we  POSTag:  PRON
interviewed  POSTag:  VERB
mostly  POSTag:  ADV
agreed  POSTag:  VERB
that  POSTag:  SCONJ
it  POSTag:  PRON
’s  POSTag:  AUX
fair  POSTag:  ADJ
to  POSTag:  PART
say  POSTag:  VERB
that  POSTag:  SCONJ
justices  POSTag:  NOUN
ask  POSTag:  VERB
more  POSTag:  ADJ
questions  POSTag:  NOUN
today  POSTag:  NOUN
than  POSTag:  SCONJ
they  POSTag:  PRON
did  POSTag:  VERB
a  POSTag:  DET
century  POSTag:  NOUN
ago  POSTag:  ADV
or  POSTag:  CCONJ
as  POSTag:  ADV
recently  POSTag:  ADV
as  POSTag:  ADP
40  POSTag:  NUM
years  POSTag:  NOUN
ago  POSTag:  ADV
.  POSTag:  PUNCT
They  POSTag:  PRON
note

Former  POSTag:  ADJ
President  POSTag:  PROPN
Clinton  POSTag:  PROPN
said  POSTag:  VERB
government  POSTag:  NOUN
got  POSTag:  VERB
the  POSTag:  DET
TARP  POSTag:  NOUN
money  POSTag:  NOUN
back  POSTag:  ADV
plus  POSTag:  CCONJ
interest  POSTag:  NOUN
.  POSTag:  PUNCT
That  POSTag:  PRON
is  POSTag:  AUX
correct  POSTag:  ADJ
for  POSTag:  ADP
the  POSTag:  DET
money  POSTag:  NOUN
that  POSTag:  PRON
went  POSTag:  VERB
to  POSTag:  ADP
banks  POSTag:  NOUN
.  POSTag:  PUNCT
It  POSTag:  PRON
is  POSTag:  AUX
incorrect  POSTag:  ADJ
for  POSTag:  ADP
TARP  POSTag:  NOUN
as  POSTag:  ADP
a  POSTag:  DET
whole  POSTag:  ADJ
.  POSTag:  PUNCT
The  POSTag:  DET
program  POSTag:  NOUN
remains  POSTag:  VERB
about  POSTag:  ADV
$  POSTag:  SYM
34  POSTag:  NUM
billion  POSTag:  NUM
in  POSTag:  ADP
the  POSTag:  DET
red  POSTag:  ADJ
.  POSTag:  PUNCT
Points  POSTag:  NOUN
of  POSTag:  ADP
Light  POSTag:  PROPN
has  POSTag:  VERB
a  POSTag:  DET
unique  POSTag:  ADJ
mission  POSTag:

Fitzsimons  POSTag:  PROPN
,  POSTag:  PUNCT
making  POSTag:  VERB
a  POSTag:  DET
point  POSTag:  NOUN
about  POSTag:  SCONJ
putting  POSTag:  VERB
women  POSTag:  NOUN
in  POSTag:  ADP
charge  POSTag:  NOUN
,  POSTag:  PUNCT
said  POSTag:  VERB
that  POSTag:  SCONJ
female  POSTag:  ADJ
buffalo  POSTag:  NOUN
lead  POSTag:  VERB
the  POSTag:  DET
herd  POSTag:  NOUN
.  POSTag:  PUNCT
Bison  POSTag:  PROPN
are  POSTag:  AUX
a  POSTag:  DET
matriarchal  POSTag:  ADJ
society  POSTag:  NOUN
,  POSTag:  PUNCT
though  POSTag:  SCONJ
female  POSTag:  ADJ
bison  POSTag:  NOUN
do  POSTag:  AUX
n’t  POSTag:  PART
lead  POSTag:  VERB
the  POSTag:  DET
entire  POSTag:  ADJ
population  POSTag:  NOUN
.  POSTag:  PUNCT
Adult  POSTag:  ADJ
males  POSTag:  NOUN
split  POSTag:  VERB
off  POSTag:  ADP
on  POSTag:  ADP
their  POSTag:  PRON
own  POSTag:  ADJ
until  POSTag:  ADP
each  POSTag:  DET
mating  POSTag:  NOUN
season  POSTag:  NOUN
,  POSTag:  PUNCT
when  POSTag:  ADV
they  POSTag:  PRON
come  POS

Rick  POSTag:  PROPN
Santorum  POSTag:  PROPN
said  POSTag:  VERB
,  POSTag:  PUNCT
"  POSTag:  PUNCT
I  POSTag:  PRON
think  POSTag:  VERB
it  POSTag:  PRON
’s  POSTag:  AUX
seven  POSTag:  NUM
or  POSTag:  CCONJ
eight  POSTag:  NUM
of  POSTag:  ADP
the  POSTag:  DET
California  POSTag:  PROPN
system  POSTag:  NOUN
of  POSTag:  ADP
universities  POSTag:  NOUN
do  POSTag:  AUX
n’t  POSTag:  PART
even  POSTag:  ADV
teach  POSTag:  VERB
an  POSTag:  DET
American  POSTag:  ADJ
history  POSTag:  NOUN
course  POSTag:  NOUN
.  POSTag:  PUNCT
It  POSTag:  PRON
’s  POSTag:  AUX
not  POSTag:  PART
even  POSTag:  ADV
available  POSTag:  ADJ
to  POSTag:  PART
be  POSTag:  AUX
taught  POSTag:  VERB
.  POSTag:  PUNCT
"  POSTag:  PUNCT
While  POSTag:  SCONJ
he  POSTag:  PRON
appeared  POSTag:  VERB
to  POSTag:  PART
be  POSTag:  AUX
referencing  POSTag:  VERB
a  POSTag:  DET
recent  POSTag:  ADJ
Wall  POSTag:  PROPN
Street  POSTag:  PROPN
Journal  POSTag:  PROPN
opinion  POSTag:  NOUN
piece  POSTag:

A  POSTag:  DET
couple  POSTag:  NOUN
of  POSTag:  ADP
Washington  POSTag:  PROPN
politicos  POSTag:  NOUN
?  POSTag:  PUNCT
Owens  POSTag:  PROPN
’  POSTag:  PART
statement  POSTag:  NOUN
rests  POSTag:  VERB
on  POSTag:  ADP
a  POSTag:  DET
1983  POSTag:  NUM
KGB  POSTag:  PROPN
memo  POSTag:  NOUN
.  POSTag:  PUNCT
The  POSTag:  DET
memo  POSTag:  NOUN
says  POSTag:  VERB
a  POSTag:  DET
friend  POSTag:  NOUN
of  POSTag:  ADP
Kennedy  POSTag:  PROPN
’s  POSTag:  PART
had  POSTag:  AUX
made  POSTag:  VERB
a  POSTag:  DET
verbal  POSTag:  ADJ
overture  POSTag:  NOUN
for  POSTag:  ADP
the  POSTag:  DET
senator  POSTag:  NOUN
to  POSTag:  PART
meet  POSTag:  VERB
with  POSTag:  ADP
Andropov  POSTag:  PROPN
as  POSTag:  ADP
part  POSTag:  NOUN
of  POSTag:  ADP
an  POSTag:  DET
effort  POSTag:  NOUN
to  POSTag:  PART
counter  POSTag:  VERB
the  POSTag:  DET
Reagan  POSTag:  PROPN
administration  POSTag:  NOUN
’s  POSTag:  PART
position  POSTag:  NOUN
on  POSTag:  ADP
nuclear  POSTag:  ADJ

In [15]:
import spacy

nlp2 = spacy.load("en_core_web_sm")

#####################
###   DEP PARSE   ###
#####################

# dep_dict = {'ACL' : 0, 'ACOMP' : 1, 'ADVCL' : 2, 'ADVMOD' : 3, 'AGENT' : 4, 
#             'AMOD' : 5, 'APPOS' : 6, 'ATTR' : 7, 'AUX' : 8, 'AUXPASS' : 9, 
#             'CASE' : 10, 'CC' : 11, 'CCOMP' : 12, 'COMPOUND' : 13, 'CONJ' : 14, 
#             'CSUBJ' : 15, 'CSUBJPASS' : 16, 'DATIVE' : 17, 'DEP' : 18, 
#             'DET' : 19, 'DOBJ' : 20, 'EXPL' : 21, 'INTJ' : 22, 'MARK' : 23, 
#             'META' : 24, 'NEG' : 25, 'NOUNMOD' : 26, 'NPMOD' : 27, 'NSUBJ' : 28, 
#             'NSUBJPASS' : 29, 'NUMMOD' : 30, 'OPRD' : 31, 'PARATAXIS' : 32, 
#             'PCOMP' : 33, 'POBJ' : 34, 'POSS' : 35, 'PRECONJ' : 36, 'PREDET' : 37, 
#             'PREP' : 38, 'PRT' : 39, 'PUNCT' : 40, 'QUANTMOD' : 41, 
#             'RELCL' : 42, 'ROOT' : 43, 'XCOMP' : 44}


dep_dict = {'punct' : 0, 'prep' : 1, 'pobj' : 2, 'compound' : 3, 'det' : 4, 
            'nsubj' : 5, 'ROOT' : 6, 'amod' : 7, 'dobj' : 8, 'aux' : 9, 
            'advmod' : 10, 'nummod' : 10, 'ccomp' : 10, 'conj' : 10, 'cc' : 10, 
            'advcl' : 10, 'poss' : 10, 'mark' : 10, 'quantmod' : 10, 'relcl' : 10, 
            'attr' : 10, 'xcomp' : 10, 'npadvmod' : 10, 'nmod' : 10, 'auxpass' : 10, 
            'acl' : 10, 'nsubjpass' : 10, 'pcomp' : 10, 'acomp' : 10, 'neg' : 10, 
            'appos' : 10, 'prt' : 10, '' : 10, 'expl' : 10, 'dative' : 10, 
            'agent' : 10, 'case' : 10, 'oprd' : 10, 'csubj' : 10, 'dep' : 10, 
            'intj' : 10, 'predet' : 10, 'parataxis' : 10, 'preconj' : 10, 
            'meta' : 10, 'csubjpass' : 10}


def get_dep_parse(statement):
    doc = nlp2(statement)
    deplist = []
    for token in doc:
#         token.text, token.lemma_, token.pos_, token.tag_, token.shape_, token.is_alpha, token.is_stop
        print(token, " ", token.dep_)
    for ent in doc.ents:
        print(ent.text, ent.label_)
    return deplist

x = data_for_pos.apply(lambda x: get_dep_parse(x))


Meantime   advmod
,   punct
    
engineering   compound
experts   nsubj
agree   ROOT
the   det
wall   nsubj
would   aux
most   advmod
likely   advmod
take   ccomp
years   dobj
to   aux
complete   relcl
.   punct
Keep   ROOT
in   prep
mind   pobj
,   punct
    
too   advmod
,   punct
    
it   nsubj
took   ROOT
more   amod
than   quantmod
six   nummod
years   dobj
to   aux
build   xcomp
roughly   advmod
700   nummod
miles   dobj
of   prep
fence   pobj
and   cc
barriers   conj
along   prep
the   det
roughly   advmod
2   nummod
,   punct
000   nummod
-   punct
mile   compound
U   pobj
.   punct
S   ROOT
.   punct
    
-   punct
Mexico   compound
border   ROOT
.   punct
years DATE
more than six years DATE
roughly 700 miles QUANTITY
roughly 2 CARDINAL
000 - mile QUANTITY
She   nsubj
cited   ROOT
layoff   compound
notices   dobj
received   acl
by   agent
the   det
state   pobj
.   punct
But   cc
those   nsubj
are   ROOT
n’t   punct
actual   amod
layoffs   attr
.   punct
And   cc
while   mark

his   poss
actions   nsubj
and   cc
words   conj
have   aux
been   ROOT
inconsistent   acomp
,   punct
    
to   prep
the   det
point   pobj
where   advmod
both   preconj
his   poss
political   amod
friends   nsubjpass
and   cc
his   poss
frequent   amod
foes   conj
on   prep
the   det
County   compound
Board   pobj
were   auxpass
taken   relcl
aback   advmod
by   agent
his   poss
withdrawal   pobj
from   prep
the   det
fight   pobj
as   mark
the   det
legislative   amod
battle   nsubj
drew   advcl
to   prep
a   det
close   pobj
in   prep
June   pobj
.   punct
Indeed   advmod
,   punct
    
if   mark
Abele   nsubj
had   advcl
the   det
nuanced   amod
position   dobj
he   nsubj
says   relcl
he   nsubj
did   ccomp
,   punct
    
it   nsubjpass
was   auxpass
so   advmod
closely   advmod
held   ROOT
that   mark
even   advmod
one   nsubj
of   prep
his   poss
top   amod
aides   pobj
apparently   advmod
was   ccomp
completely   advmod
unaware   acomp
of   prep
it   pobj
.   punct
Milwaukee Co

after   prep
which   pobj
Obama   nsubj
would   aux
consider   relcl
using   xcomp
military   amod
force   dobj
in   prep
Syria   pobj
.   punct
In   prep
the   det
months   pobj
following   prep
that   det
statement   pobj
,   punct
    
Clinton   nsubj
reiterated   ROOT
Obama   compound
’s   compound
position   dobj
,   punct
    
using   advcl
the   det
phrase   dobj
    
"   punct
red   amod
line   dobj
.   punct
    
"   ROOT
A   det
year   npadvmod
later   advmod
,   punct
    
August   npadvmod
2013   nummod
,   punct
    
the   det
White   compound
House   nsubj
confirmed   ROOT
Syria   nsubj
had   aux
crossed   ccomp
this   det
    
"   punct
red   amod
line   dobj
.   punct
    
"   ROOT
By   prep
this   det
point   pobj
,   punct
    
Clinton   nsubj
had   aux
left   ROOT
the   det
State   compound
Department   dobj
months   npadvmod
earlier   advmod
.   punct
However   advmod
,   punct
    
in   prep
the   det
days   pobj
following   prep
that   det
revelation   pobj
,   pu

.   punct
S   ROOT
.   punct
    
73rd   ROOT
among   prep
109   nummod
nations   pobj
and   cc
territories   conj
.   punct
Locke ORG
The United States GPE
Pew GPE
31st ORDINAL
34 CARDINAL
OECD ORG
Wider PRODUCT
the International Institute for Democracy and Electoral Assistance ORG
73rd ORDINAL
109 CARDINAL
Cain   nsubj
said   ROOT
that   mark
Thomas   compound
Jefferson   nsubj
said   ccomp
,   punct
     
"   punct
You   nsubj
might   aux
be   ccomp
able   acomp
to   aux
fool   xcomp
the   det
people   dobj
for   prep
a   det
while   pobj
,   punct
    
and   cc
they   nsubj
may   aux
go   conj
astray   advmod
,   punct
    
but   cc
sooner   advmod
or   cc
later   conj
the   det
American   amod
people   nsubj
are   aux
going   conj
to   aux
wake   xcomp
up   prt
and   cc
they   nsubj
will   aux
correct   conj
the   det
course   dobj
.   punct
    
"   ROOT
Jefferson   nsubj
did   aux
write   ROOT
a   det
line   dobj
that   nsubj
resembles   relcl
that   mark
in   prep
some   det
im

to   aux
get   advcl
the   det
protection   dobj
.   punct
Romney ORG
Romney ORG
Romney ORG
Bernie   nsubj
,   punct
    
a   det
Doonesbury   compound
character   appos
,   punct
    
said   ROOT
Abbott   intj
    
"   punct
activated   ccomp
the   det
state   compound
guard   dobj
to   aux
monitor   advcl
"   punct
    
Jade   compound
Helm   dobj
15   nummod
    
"   punct
in   prep
case   pobj
the   det
troops   nsubj
try   relcl
to   aux
impose   xcomp
martial   amod
law   dobj
,   punct
    
disarm   conj
innocent   amod
Texans   dobj
,   punct
    
and   cc
detain   conj
them   dobj
in   prep
tunnels   pobj
beneath   prep
closed   amod
Walmart   compound
stores   pobj
.   punct
    
"   ROOT
Abbott   nsubj
told   ROOT
the   det
Guard   dobj
to   aux
monitor   xcomp
the   det
exercise   dobj
though   advmod
far   advmod
as   mark
we   nsubj
can   aux
tell   advcl
,   punct
    
no   det
troops   nsubjpass
were   auxpass
dispatched   ccomp
or   cc
activated   conj
.   punct
It   n

...

them   dobj
in   prep
an   det
entirely   advmod
different   amod
context   pobj
.   punct
What   dobj
Romney   nsubj
actually   advmod
said   csubj
was   ROOT
,   punct
     
"   punct
I   nsubj
like   ccomp
being   pcomp
able   acomp
to   aux
fire   xcomp
people   dobj
who   nsubj
provide   relcl
services   dobj
to   dative
me   pobj
,   punct
    
"   punct
    
and   cc
he   nsubj
was   aux
talking   conj
specifically   advmod
about   prep
switching   pcomp
health   compound
insurance   compound
companies   dobj
if   mark
a   det
provider   nsubj
is   aux
n’t   punct
giving   advcl
good   amod
service   dobj
.   punct
Markell ORG
Mitt Romney PERSON
Mitt Romney PERSON
Mitt Romney PERSON
Romney ORG
Romney ORG
Right   advmod
now   advmod
,   punct
    
there   expl
seems   ROOT
to   aux
be   xcomp
no   det
viable   amod
legislative   amod
solution   attr
in   prep
sight   pobj
.   punct
To   aux
sum   advcl
up   prt
,   punct
    
McCallum   nsubj
said   ROOT
a   det
child   nsubj
bor

us   dobj
to   prep
a   det
credible   amod
March   nmod
2015   nummod
study   pobj
that   nsubj
supports   relcl
his   poss
point   dobj
.   punct
According   prep
to   prep
the   det
study   pobj
,   punct
    
a   det
drought   nsubj
in   prep
Syria   pobj
in   prep
the   det
2000s   pobj
displaced   ROOT
millions   dobj
of   prep
refugees   pobj
and   cc
added   conj
to   prep
discontent   pobj
that   nsubj
eventually   advmod
erupted   ccomp
into   prep
war   pobj
.   punct
While   mark
the   det
study   nsubj
does   aux
not   neg
mention   advcl
ISIS   dobj
by   prep
name   pobj
,   punct
    
the   det
authors   nsubj
say   ROOT
O’Malley   nsubj
is   aux
simply   advmod
taking   ccomp
their   poss
argument   dobj
one   nummod
step   npadvmod
further   advmod
.   punct
Experts   nsubj
agreed   ROOT
that   mark
the   det
drought   nsubj
,   punct
    
spurred   acl
by   agent
climate   compound
change   pobj
,   punct
    
was   ccomp
one   attr
of   prep
many   amod
factors   pob

and   cc
Obama   conj
on   prep
an   det
issue   pobj
such   amod
as   prep
those   pobj
listed   acl
at   prep
the   det
start   pobj
of   prep
the   det
ad   pobj
    
-   punct
    
-   punct
    
he   nsubj
said   ROOT
they   nsubj
both   appos
used   ccomp
a   det
familiar   amod
campaign   compound
tactic   dobj
,   punct
    
throwing   advcl
    
"   punct
bombs   dobj
"   punct
    
about   prep
something   pobj
they   nsubj
did   aux
n't   neg
have   relcl
to   aux
vote   xcomp
on   prep
themselves   pobj
.   punct
The   det
ad   nsubj
provides   ROOT
no   det
explanation   dobj
for   prep
how   advmod
he   nsubj
compared   pcomp
the   det
two   nummod
politicians   dobj
and   cc
neglects   conj
to   aux
note   xcomp
that   mark
LeMieux   nsubj
supported   ccomp
Rubio   poss
's   case
campaign   dobj
once   mark
Crist   nsubj
left   advcl
the   det
GOP   dobj
.   punct
LeMieux ORG
Rubio and Obama ORG
two CARDINAL
LeMieux ORG
Rubio ORG
Crist PERSON
GOP ORG
After   prep
making 

,   punct
    
he   nsubj
bungled   ROOT
the   det
details   dobj
    
—   ROOT
    
and   cc
badly   conj
.   punct
Far   advmod
from   ROOT
    
"   punct
not   neg
available   conj
,   punct
    
"   punct
    
American   amod
history   compound
courses   nsubjpass
are   auxpass
offered   ROOT
at   advmod
all   advmod
but   prep
one   pobj
of   prep
33   nummod
state   compound
universities   pobj
in   prep
California   pobj
.   punct
Rick Santorum PERSON
seven CARDINAL
eight CARDINAL
California GPE
American NORP
Wall Street Journal ORG
American NORP
one CARDINAL
33 CARDINAL
California GPE
That   nsubj
’s   ROOT
a   det
distortion   dobj
of   prep
the   det
truth   pobj
.   punct
Menendez   nsubj
voted   ROOT
in   prep
favor   pobj
of   prep
a   det
bill   pobj
tied   acl
to   prep
the   det
health   compound
care   compound
law   pobj
that   nsubj
created   relcl
a   det
tax   dobj
on   prep
investment   compound
income   pobj
for   prep
high   amod
-   punct
income   compound
earn

has   aux
since   advmod
backed   conj
off   prt
that   det
plan   dobj
.   punct
His   poss
new   amod
proposal   nsubjpass
is   auxpass
based   ROOT
on   prep
the   det
property   compound
tax   compound
burden   pobj
of   prep
homeowners   pobj
and   cc
excludes   conj
residents   dobj
with   prep
incomes   pobj
more   advmod
than   prep
    
$   nmod
400   dep
,   punct
000   dep
.   punct
400 MONEY
000 CARDINAL
